## EDA & Preparation

> In this notebook we explored data, cleaned it, transformed it, and prepared a dataset we will use to work with our Machine Learning Hypothesis (that we can use this dataset to predict if a customer will have a future purchase).

### Exploratory Data Analysis

The first thing we'll do is explore the data. We will use a tool named `Pandas profiler` to quickly and easily explore the columns, statistics, and distributions of our data. We will also go ahead with some data cleaning and transformations.

In [2]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
import matplotlib.pyplot as plt

In [3]:
# Provide the relative file path to the CSV file
file_path = "../data/OnlineRetail.csv"

# Read the CSV file into a DataFrame, specifying the encoding
df = pd.read_csv(file_path, encoding='latin1')

df.head()

InvoiceNo StockCode                          Description  Quantity  \
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

      InvoiceDate  UnitPrice  CustomerID         Country  
0  12/1/2010 8:26       2.55     17850.0  United Kingdom  
1  12/1/2010 8:26       3.39     17850.0  United Kingdom  
2  12/1/2010 8:26       2.75     17850.0  United Kingdom  
3  12/1/2010 8:26       3.39     17850.0  United Kingdom  
4  12/1/2010 8:26       3.39     17850.0  United Kingdom

In [4]:
# We'll keep track of our transformations.
# [1] Transform InvoiceDate to a date type:
df['InvoiceDate'] = pd.to_datetime(df['InvoiceDate'])

In [5]:
# Profiling data
original_report = ProfileReport(df, title="Profiling Report Online Retail")

In [20]:
original_report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
# Check data frame information:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 541909 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   InvoiceNo    541909 non-null  object        
 1   StockCode    541909 non-null  object        
 2   Description  540455 non-null  object        
 3   Quantity     541909 non-null  int64         
 4   InvoiceDate  541909 non-null  datetime64[ns]
 5   UnitPrice    541909 non-null  float64       
 6   CustomerID   406829 non-null  float64       
 7   Country      541909 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(1), object(4)
memory usage: 33.1+ MB


We can see that the only columns with null values are `Description` and `CustomerID`. 


In [7]:
print(f'Percentage of Null values for CustomerID: {np.round(df["CustomerID"].isnull().sum()/df["CustomerID"].shape[0] * 100, 2)}% ({df["CustomerID"].isnull().sum()} rows)')

Percentage of Null values for CustomerID: 24.93% (135080 rows)


In [8]:
print(f'Percentage of Null values for Description: {np.round(df["Description"].isnull().sum()/df["Description"].shape[0] * 100, 2)}% ({df["Description"].isnull().sum()} rows)')

Percentage of Null values for Description: 0.27% (1454 rows)


In [9]:
df[df['CustomerID'].isnull()].head()

InvoiceNo StockCode                      Description  Quantity  \
622     536414     22139                              NaN        56   
1443    536544     21773  DECORATIVE ROSE BATHROOM BOTTLE         1   
1444    536544     21774  DECORATIVE CATS BATHROOM BOTTLE         2   
1445    536544     21786               POLKADOT RAIN HAT          4   
1446    536544     21787            RAIN PONCHO RETROSPOT         2   

             InvoiceDate  UnitPrice  CustomerID         Country  
622  2010-12-01 11:52:00       0.00         NaN  United Kingdom  
1443 2010-12-01 14:32:00       2.51         NaN  United Kingdom  
1444 2010-12-01 14:32:00       2.51         NaN  United Kingdom  
1445 2010-12-01 14:32:00       0.85         NaN  United Kingdom  
1446 2010-12-01 14:32:00       1.66         NaN  United Kingdom

In [10]:
null_df = df[df['CustomerID'].isnull()]
null_df['CustomerID'] = 0

# Analyzing data for null values
null_report = ProfileReport(null_df, title="Profiling Report Null CustomerID Observations")

/var/folders/wy/gf9gm29n7dqgd0s3x_1tysr00000gn/T/ipykernel_54361/4098901780.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  null_df['CustomerID'] = 0


In [30]:
original_report.compare(null_report)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

We can observe how the `1454` rows with missing values on `Description` also have missing values is `CustomerID`. We compared the behavior of the rest of the variables in the rows with missing `CustomerID` and did not find any particular behavior. The missing `CustomerID` seems to be a capture error. As tracking a purchase history is fundamental for our analysis, we will proceed with dropping the rows that couldn't be associated with a customer's history.

In [11]:
# [2] Eliminate null values.
df = df.dropna()
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 406829 entries, 0 to 541908
Data columns (total 8 columns):
 #   Column       Non-Null Count   Dtype         
---  ------       --------------   -----         
 0   InvoiceNo    406829 non-null  object        
 1   StockCode    406829 non-null  object        
 2   Description  406829 non-null  object        
 3   Quantity     406829 non-null  int64         
 4   InvoiceDate  406829 non-null  datetime64[ns]
 5   UnitPrice    406829 non-null  float64       
 6   CustomerID   406829 non-null  float64       
 7   Country      406829 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(1), object(4)
memory usage: 27.9+ MB


Now, let's proceed with the analysis (using our profiler report). We can observe how we have 4879 rows are duplicates. 

In [12]:
# [3] Eliminate duplicate rows:
df = df.drop_duplicates()

We see that 91% of our market is the United Kingdom. As we have 1 day to create a model for the business, we recommend continuing with the analysis just for the UK. If the business likes the MVP we can explore using Machine Learning to predict customer purchases in other markets (or using the `Country` as a variable, we might revisit later).

In [13]:
# [4] Get only UK data
df_uk = df.query("Country=='United Kingdom'").drop(['Country'], axis=1).reset_index(drop=True)

In [46]:
uk_report = ProfileReport(df_uk, title="Profiling Report UK")
uk_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Another alert we got in our profiler is the skew in the `UnitPrice`. When checking the details we see we have a mean of 3.26, 95th percentile of 8.5 and a maximum of 38970. Let's check if we have outliers in that variable.

In [14]:
p = 0.9995
print(f'{p*100}% of the data has a UnitPrice below {df.UnitPrice.quantile(p)}')

99.95% of the data has a UnitPrice below 150.0


Let's manually explore high values of `UnitPrice`.

In [31]:
df_uk.query('UnitPrice > 150')

InvoiceNo StockCode                         Description  Quantity  \
203       536392     22827  RUSTIC  SEVENTEEN DRAWER SIDEBOARD         1   
3489      536835     22655         VINTAGE RED KITCHEN CABINET         1   
11456     537859     22828        REGENCY MIRROR WITH SHUTTERS         1   
14175     538354     22826       LOVE SEAT ANTIQUE WHITE METAL         2   
19605     539080     22655         VINTAGE RED KITCHEN CABINET         1   
...          ...       ...                                 ...       ...   
308862    577130     22827  RUSTIC  SEVENTEEN DRAWER SIDEBOARD         1   
320089    578270       DOT                      DOTCOM POSTAGE         1   
329287    579196       DOT                      DOTCOM POSTAGE         1   
340431    580645         M                              Manual         1   
342388    580727       DOT                      DOTCOM POSTAGE         1   

               InvoiceDate  UnitPrice  CustomerID  
203    2010-12-01 10:29:00     165.00     13705.0  
3489   2010-12-02 18:06:00     295.00     13145.0  
11456  2010-12-08 16:11:00     165.00     14030.0  
14175  2010-12-10 15:45:00     175.00     16873.0  
19605  2010-12-16 08:41:00     295.00     16607.0  
...                    ...        ...         ...  
308862 2011-11-17 19:58:00     165.00     15861.0  
320089 2011-11-23 13:39:00    1270.06     14096.0  
329287 2011-11-28 15:54:00    1526.76     14096.0  
340431 2011-12-05 13:11:00     219.50     17857.0  
342388 2011-12-05 17:17:00    1599.26     14096.0  

[72 rows x 7 columns]

In [15]:
df_uk.query('UnitPrice > 500')

InvoiceNo StockCode                     Description  Quantity  \
49114    C543789         M                          Manual        -1   
91097    C549452         D                        Discount        -1   
91107     549468         M                          Manual         1   
106841   C551685      POST                         POSTAGE        -1   
106939    551697      POST                         POSTAGE         1   
106948   C551699         M                          Manual        -1   
115511   C552876         M                          Manual        -1   
139430   C556274         M                          Manual        -1   
140085    556444     22502  PICNIC BASKET WICKER 60 PIECES        60   
140086   C556445         M                          Manual        -1   
140087    556446     22502  PICNIC BASKET WICKER 60 PIECES         1   
148631   C557638      POST                         POSTAGE        -1   
153752    558381         M                          Manual         1   
168252   C560372         M                          Manual        -1   
168485   C560408         M                          Manual        -1   
168575    560413         M                          Manual         1   
168576   C560414         M                          Manual        -1   
168605   C560418         M                          Manual        -1   
168606   C560420         M                          Manual        -1   
168644   C560430         M                          Manual        -1   
168661   C560436         M                          Manual        -1   
170024   C560647         M                          Manual        -1   
185258   C562647         M                          Manual        -1   
187368    562946         M                          Manual         1   
204704    565377         M                          Manual         1   
218573   C566925         M                          Manual        -1   
218577    566927         M                          Manual         1   
224288    567656       DOT                  DOTCOM POSTAGE         1   
224692   C567655      CRUK                 CRUK Commission        -1   
231969    568346       DOT                  DOTCOM POSTAGE         1   
241663    569382         M                          Manual         1   
251241   C570301         M                          Manual        -1   
253146    570488       DOT                  DOTCOM POSTAGE         1   
260781    571441       DOT                  DOTCOM POSTAGE         1   
271485    572552       DOT                  DOTCOM POSTAGE         1   
277644   C573268         M                          Manual        -1   
281931    573576       DOT                  DOTCOM POSTAGE         1   
282339   C573575      CRUK                 CRUK Commission        -1   
300024    575607       DOT                  DOTCOM POSTAGE         1   
300047   C575606      CRUK                 CRUK Commission        -1   
308601    576339       DOT                  DOTCOM POSTAGE         1   
308602   C576338      CRUK                 CRUK Commission        -1   
309047    576389         M                          Manual         1   
327125    578270       DOT                  DOTCOM POSTAGE         1   
327142   C578269      CRUK                 CRUK Commission        -1   
336433    579196       DOT                  DOTCOM POSTAGE         1   
336535   C579195      CRUK                 CRUK Commission        -1   
349733    580727       DOT                  DOTCOM POSTAGE         1   
349738   C580726      CRUK                 CRUK Commission        -1   

               InvoiceDate  UnitPrice  CustomerID  
49114  2011-02-11 17:10:00     856.48     17450.0  
91097  2011-04-08 14:17:00    1867.86     17940.0  
91107  2011-04-08 14:27:00    1867.86     17940.0  
106841 2011-05-03 12:51:00    8142.75     16029.0  
106939 2011-05-03 13:46:00    8142.75     16029.0  
106948 2011-05-03 14:12:00    6930.00     16029.0  
115511 2011-05-12 09:48:00     929.90     

We can see how most of the outlier values have a description of 'Manual', 'DOTCOM POSTAGE', 'POSTAGE', 'Discount', or 'CRUK Commission' (descriptions as 'PICNIC BASKET WICKER 60 PIECES' are viable products).

In [16]:
df_uk[df_uk['Description']=='Manual']

InvoiceNo StockCode Description  Quantity         InvoiceDate  \
1495      536569         M      Manual         1 2010-12-01 15:35:00   
1506      536569         M      Manual         1 2010-12-01 15:35:00   
4304      536981         M      Manual         2 2010-12-03 14:26:00   
5155      537077         M      Manual        12 2010-12-05 11:59:00   
5664      537137         M      Manual        36 2010-12-05 12:43:00   
...          ...       ...         ...       ...                 ...   
351428    580956         M      Manual         4 2011-12-06 14:23:00   
352210   C581009         M      Manual        -1 2011-12-07 09:15:00   
353152   C581145         M      Manual        -1 2011-12-07 13:48:00   
355087    581405         M      Manual         3 2011-12-08 13:50:00   
356446   C581499         M      Manual        -1 2011-12-09 10:28:00   

        UnitPrice  CustomerID  
1495         1.25     16274.0  
1506        18.95     16274.0  
4304         0.85     14723.0  
5155         0.42     17062.0  
5664         0.85     16327.0  
...           ...         ...  
351428       1.25     17841.0  
352210     125.00     16971.0  
353152       9.95     17490.0  
355087       0.42     13521.0  
356446     224.69     15498.0  

[380 rows x 7 columns]

We see how for these descriptions we may have a variety of UnitPrices, which means we it's not the cause of the anomalous behavior. But we could have a situation were the values `Quantity` and `UnitPrice` were not correctly logged in.

We will opt for not removing outlier rows as we don't want to misrepresent products with a high price as furniture. But we noticed that the `StockCode` is not numeric for some of the outlier values. And from the profiling statistics we see that we have numeric values of 6-12 characters. So we 

In [43]:
df_uk[df_uk['StockCode'].str.len() < 5].Description.unique()

array(['Manual', 'CARRIAGE', 'POSTAGE', 'PADS TO MATCH ALL CUSHIONS',
       'DOTCOM POSTAGE'], dtype=object)

In [42]:
df_uk[df_uk['StockCode'].str.len() < 5].StockCode.unique()

array(['M', 'C2', 'POST', 'PADS', 'DOT'], dtype=object)

In [49]:
df_uk.query('StockCode=="M"')

InvoiceNo StockCode Description  Quantity         InvoiceDate  \
1483      536569         M      Manual         1 2010-12-01 15:35:00   
1494      536569         M      Manual         1 2010-12-01 15:35:00   
4238      536981         M      Manual         2 2010-12-03 14:26:00   
5083      537077         M      Manual        12 2010-12-05 11:59:00   
5586      537137         M      Manual        36 2010-12-05 12:43:00   
...          ...       ...         ...       ...                 ...   
340431    580645         M      Manual         1 2011-12-05 13:11:00   
340434    580646         M      Manual       800 2011-12-05 13:13:00   
343534    580884         M      Manual         1 2011-12-06 12:21:00   
344024    580956         M      Manual         4 2011-12-06 14:23:00   
347612    581405         M      Manual         3 2011-12-08 13:50:00   

        UnitPrice  CustomerID  
1483         1.25     16274.0  
1494        18.95     16274.0  
4238         0.85     14723.0  
5083         0.42     17062.0  
5586         0.85     16327.0  
...           ...         ...  
340431     219.50     17857.0  
340434       0.25     17857.0  
343534       0.85     15907.0  
344024       1.25     17841.0  
347612       0.42     13521.0  

[246 rows x 7 columns]

We notice that "PADS", "DOT", and "POST" are rows that will not be helpful in our analysis as they seem to be system transactions different from regular purchases. And regarding manual transactions, we will opt to remove them as we will use the `Description` text as input of our model (use text embeddings as a feature), so we would need more work to input those missing values (imputing missing values with statistic of other embeddings).

In [51]:
# [5] Remove columns:
df_uk.drop(df_uk.query('StockCode == "M" | StockCode == "POST" | StockCode == "PADS" | StockCode == "DOT"').index, axis = 0, inplace = True)

In [53]:
# [6] Reset index
df_uk = df_uk.reset_index(drop=True)

InvoiceNo StockCode                          Description  Quantity  \
0         536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6   
1         536365     71053                  WHITE METAL LANTERN         6   
2         536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3         536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4         536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   
...          ...       ...                                  ...       ...   
348929    581585     22466       FAIRY TALE COTTAGE NIGHT LIGHT        12   
348930    581586     22061  LARGE CAKE STAND  HANGING STRAWBERY         8   
348931    581586     23275     SET OF 3 HANGING OWLS OLLIE BEAK        24   
348932    581586     21217        RED RETROSPOT ROUND CAKE TINS        24   
348933    581586     20685                DOORMAT RED RETROSPOT        10   

               InvoiceDate  UnitPrice  CustomerID  
0      2010-12-01 08:26:00       2.55     17850.0  
1      2010-12-01 08:26:00       3.39     17850.0  
2      2010-12-01 08:26:00       2.75     17850.0  
3      2010-12-01 08:26:00       3.39     17850.0  
4      2010-12-01 08:26:00       3.39     17850.0  
...                    ...        ...         ...  
348929 2011-12-09 12:31:00       1.95     15804.0  
348930 2011-12-09 12:49:00       2.95     13113.0  
348931 2011-12-09 12:49:00       1.25     13113.0  
348932 2011-12-09 12:49:00       8.95     13113.0  
348933 2011-12-09 12:49:00       7.08     13113.0  

[348934 rows x 7 columns]

The next thing that we'll check is `Quantity`. We see that 2.1% of the data is negative.

In [17]:
df_uk.query('Quantity < 0')

InvoiceNo StockCode                       Description  Quantity  \
121      C536379         D                          Discount        -1   
134      C536383    35004C   SET OF 3 COLOURED  FLYING DUCKS        -1   
201      C536391     22556    PLASTERS IN TIN CIRCUS PARADE        -12   
202      C536391     21984  PACK OF 12 PINK PAISLEY TISSUES        -24   
203      C536391     21983  PACK OF 12 BLUE PAISLEY TISSUES        -24   
...          ...       ...                               ...       ...   
356398   C581490     23144   ZINC T-LIGHT HOLDER STARS SMALL       -11   
356446   C581499         M                            Manual        -1   
356613   C581568     21258        VICTORIAN SEWING BOX LARGE        -5   
356614   C581569     84978  HANGING HEART JAR T-LIGHT HOLDER        -1   
356615   C581569     20979     36 PENCILS TUBE RED RETROSPOT        -5   

               InvoiceDate  UnitPrice  CustomerID  
121    2010-12-01 09:41:00      27.50     14527.0  
134    2010-12-01 09:49:00       4.65     15311.0  
201    2010-12-01 10:24:00       1.65     17548.0  
202    2010-12-01 10:24:00       0.29     17548.0  
203    2010-12-01 10:24:00       0.29     17548.0  
...                    ...        ...         ...  
356398 2011-12-09 09:57:00       0.83     14397.0  
356446 2011-12-09 10:28:00     224.69     15498.0  
356613 2011-12-09 11:57:00      10.95     15311.0  
356614 2011-12-09 11:58:00       1.25     17315.0  
356615 2011-12-09 11:58:00       1.25     17315.0  

[7501 rows x 7 columns]

In [20]:
df_uk[df_uk['InvoiceNo'].str.contains("C")].InvoiceNo.count()

7501

We can see that the number of rows with negative `Quantity` is the same number of rows with a C in the Invoice Number. May be referring to the retail store cancellations. We will eliminate this rows, but not the rows of the original buys as what we care about is further purchases, right now we will not deal with wether a purchase is cancelled as there might be several reason of the cancellation.

In [24]:
# To confirm:
df_uk[(df_uk['InvoiceNo'].str.contains("C")) & (df_uk['Quantity']<0)].InvoiceNo.count()

7501

In [25]:
# [7] Positive quantity:
df_uk = df_uk.query("Quantity>0").reset_index(drop=True)

In [54]:
df_uk.Quantity.describe()

count    348934.000000
mean         12.171591
std         191.836297
min           1.000000
25%           2.000000
50%           4.000000
75%          12.000000
max       80995.000000
Name: Quantity, dtype: float64

In [27]:
p = 0.95
print(f'{p*100}% of the data has a UnitPrice below {df.Quantity.quantile(p)}')

95.0% of the data has a UnitPrice below 36.0


In [30]:
df_uk.query('Quantity > 5000')

InvoiceNo StockCode                     Description  Quantity  \
32817     541431     23166  MEDIUM CERAMIC TOP STORAGE JAR     74215   
324530    578841     84826  ASSTD DESIGN 3D PAPER STICKERS     12540   
348876    581483     23843     PAPER CRAFT , LITTLE BIRDIE     80995   

               InvoiceDate  UnitPrice  CustomerID  
32817  2011-01-18 10:01:00       1.04     12346.0  
324530 2011-11-25 15:57:00       0.00     13256.0  
348876 2011-12-09 09:15:00       2.08     16446.0

We notice there are customers that buy products in very large quantities. In retail there is a whole section of analysis name **'Pro Customers'**. That, depending on the retail's store line of business, they have businesses that make them buy very high quantities of product. In this study we will not focus on the idea, but it is important to notice as it could be a next step in the modeling of "purchase intent": analyzing and identifying pro customers.

For now, as we did with `UnitPrice`, we will leave the high values and remove them if needed.

### Create a Label and Purchase History Features

Now, let's go back to our modeling objective. We want to predict if a customer will make a future purchase. For this, we need to create a label and features.

In [56]:
# [8] Purchase history for each customer
df_uk["PurchaseNumber"] = df_uk.groupby("CustomerID")["InvoiceDate"].rank(method="dense", ascending=True)


In [60]:
df_uk.sort_values(by=['PurchaseNumber'], ascending=False).head()

InvoiceNo StockCode                     Description  Quantity  \
349181    581580     22908   PACK OF 20 NAPKINS RED APPLES         2   
349179    581580     22695             WICKER WREATH SMALL         1   
349180    581580     22144  CHRISTMAS CRAFT LITTLE FRIENDS         1   
349169    581580     23334        IVORY WICKER HEART SMALL         4   
349170    581580     21790              VINTAGE SNAP CARDS         1   

               InvoiceDate  UnitPrice  CustomerID  PurchaseNumber  
349181 2011-12-09 12:20:00       0.85     12748.0           207.0  
349179 2011-12-09 12:20:00       0.59     12748.0           207.0  
349180 2011-12-09 12:20:00       2.10     12748.0           207.0  
349169 2011-12-09 12:20:00       0.63     12748.0           207.0  
349170 2011-12-09 12:20:00       0.85     12748.0           207.0

In [69]:
# [9] Get latest purchase for each CustomerID
latest_purchase_df = df_uk.groupby('CustomerID').agg({
    'PurchaseNumber': 'max'
})
latest_purchase_df.rename(columns={"PurchaseNumber": "CustomerLatestPurchase", "lastname": "LASTNAME"}, inplace=True)
# Reset the index of the grouped DataFrame
latest_purchase_df = latest_purchase_df.reset_index()

In [70]:
latest_purchase_df

CustomerID  CustomerLatestPurchase
0        12346.0                     1.0
1        12747.0                    11.0
2        12748.0                   207.0
3        12749.0                     5.0
4        12820.0                     4.0
...          ...                     ...
3913     18280.0                     1.0
3914     18281.0                     1.0
3915     18282.0                     2.0
3916     18283.0                    16.0
3917     18287.0                     3.0

[3918 rows x 2 columns]

In [79]:
# [10] Merge with data frame
df_uk = pd.merge(df_uk,latest_purchase_df,on='CustomerID',how='left')

In here we realize that for our objective we will need to aggregate our rows to have **one row per InvoiceNo**. But first, let's obtain the total paid per product transaction (quantity * unit price).

In [72]:
# [11] Get total paid
df_uk["TotalPaid"] =  df_uk["UnitPrice"] * df_uk["Quantity"]

In [80]:
#[12] Group by Invoice
grouped_df = df_uk.groupby('InvoiceNo').agg({
    'Description': lambda x: ' '.join(x),
    'TotalPaid': 'sum',
    'InvoiceDate': 'max',
    'PurchaseNumber': 'max',
    'CustomerLatestPurchase': 'max',
})

# Reset the index of the grouped DataFrame
grouped_df = grouped_df.reset_index()

In [81]:
grouped_df

InvoiceNo                                        Description  TotalPaid  \
0        536365  WHITE HANGING HEART T-LIGHT HOLDER WHITE METAL...     139.12   
1        536366   HAND WARMER UNION JACK HAND WARMER RED POLKA DOT      22.20   
2        536367  ASSORTED COLOUR BIRD ORNAMENT POPPY'S PLAYHOUS...     278.73   
3        536368  JAM MAKING SET WITH JARS RED COAT RACK PARIS F...      70.05   
4        536369                           BATH BUILDING BLOCK WORD      17.85   
...         ...                                                ...        ...   
16587    581582  BICYCLE PUNCTURE REPAIR KIT  CLASSIC BICYCLE C...      29.88   
16588    581583  LUNCH BAG RED RETROSPOT 6 CHOCOLATE LOVE HEART...     124.60   
16589    581584  RED FLOCK LOVE HEART PHOTO FRAME 6 CHOCOLATE L...     140.64   
16590    581585  BLACK TEA TOWEL CLASSIC DESIGN ASSORTED BOTTLE...     329.05   
16591    581586  LARGE CAKE STAND  HANGING STRAWBERY SET OF 3 H...     339.20   

              InvoiceDate  PurchaseNumber  CustomerLatestPurchase  
0     2010-12-01 08:26:00             1.0                    33.0  
1     2010-12-01 08:28:00             2.0                    33.0  
2     2010-12-01 08:34:00             1.0                     8.0  
3     2010-12-01 08:34:00             1.0                     8.0  
4     2010-12-01 08:35:00             2.0                     8.0  
...                   ...             ...                     ...  
16587 2011-12-09 12:21:00            24.0                    24.0  
16588 2011-12-09 12:23:00            31.0                    32.0  
16589 2011-12-09 12:25:00            32.0                    32.0  
16590 2011-12-09 12:31:00            13.0                    13.0  
16591 2011-12-09 12:49:00            24.0                    24.0  

[16592 rows x 6 columns]

In [82]:
# Validation
len(grouped_df.InvoiceNo.unique())

16592

Now, to create the **label** we will compare the purchase number with the latest purchase.

In [83]:
# [13] Create the 'FuturePurchase' column based on the conditions
grouped_df['FuturePurchase'] = np.where(grouped_df['PurchaseNumber'] < grouped_df['CustomerLatestPurchase'], 1, 0)

In [84]:
grouped_df

InvoiceNo                                        Description  TotalPaid  \
0        536365  WHITE HANGING HEART T-LIGHT HOLDER WHITE METAL...     139.12   
1        536366   HAND WARMER UNION JACK HAND WARMER RED POLKA DOT      22.20   
2        536367  ASSORTED COLOUR BIRD ORNAMENT POPPY'S PLAYHOUS...     278.73   
3        536368  JAM MAKING SET WITH JARS RED COAT RACK PARIS F...      70.05   
4        536369                           BATH BUILDING BLOCK WORD      17.85   
...         ...                                                ...        ...   
16587    581582  BICYCLE PUNCTURE REPAIR KIT  CLASSIC BICYCLE C...      29.88   
16588    581583  LUNCH BAG RED RETROSPOT 6 CHOCOLATE LOVE HEART...     124.60   
16589    581584  RED FLOCK LOVE HEART PHOTO FRAME 6 CHOCOLATE L...     140.64   
16590    581585  BLACK TEA TOWEL CLASSIC DESIGN ASSORTED BOTTLE...     329.05   
16591    581586  LARGE CAKE STAND  HANGING STRAWBERY SET OF 3 H...     339.20   

              InvoiceDate  PurchaseNumber  CustomerLatestPurchase  \
0     2010-12-01 08:26:00             1.0                    33.0   
1     2010-12-01 08:28:00             2.0                    33.0   
2     2010-12-01 08:34:00             1.0                     8.0   
3     2010-12-01 08:34:00             1.0                     8.0   
4     2010-12-01 08:35:00             2.0                     8.0   
...                   ...             ...                     ...   
16587 2011-12-09 12:21:00            24.0                    24.0   
16588 2011-12-09 12:23:00            31.0                    32.0   
16589 2011-12-09 12:25:00            32.0                    32.0   
16590 2011-12-09 12:31:00            13.0                    13.0   
16591 2011-12-09 12:49:00            24.0                    24.0   

       FuturePurchase  
0                   1  
1                   1  
2                   1  
3                   1  
4                   1  
...               ...  
16587               0  
16588               1  
16589               0  
16590               0  
16591               0  

[16592 rows x 7 columns]

Let's check the distribution of our label:

In [87]:
grouped_df.FuturePurchase.value_counts(normalize=True)

FuturePurchase
1    0.763259
0    0.236741
Name: proportion, dtype: float64

In [88]:
# [14] Get data for modeling
model_df = grouped_df[['Description', 'TotalPaid', 'InvoiceDate', 'PurchaseNumber', 'FuturePurchase']]

For the next step we will export this data and go ahead test it with an AutoML model (this will save ud the task of further preprocessing and analyzing our features). Having more time we can expand our analysis and try some custom models. We could also experiment with features to add variables that introduce time between purchases.

In [89]:
file_path = "../data/ModelData.csv"
model_df.to_csv(file_path, index=False)